## Creating interactive maps using python 

#### Importing required libraries

In [5]:
import os
import pandas as pd
# from folium.plugins import MarkerCluster, Search, MiniMap
#from folium import IFrame, Map, GeoJson, features, Marker, Popup, LayerControl
import folium.plugins as plugins
import folium

#### Data import and processing section

In [6]:
# First we will load indiviual apartments data store in blore_apartment_data.csv
Indiviual_apartments = pd.read_csv('blore_apartment_data.csv')
Indiviual_apartments.head()

names             Price             Area  \
0  Salarpuria Sattva Cadenza     39 L -41.65 L        755 sq.ft   
1  Salarpuria Sattva Cadenza        55 L -75 L  1175-1275 sq.ft   
2  Salarpuria Sattva Cadenza  70.04 L -73.30 L  1335-1340 sq.ft   
3  Salarpuria Sattva Cadenza        65 L -95 L  1365-1595 sq.ft   
4              Purva Skydale  76.25 L -1.75 Cr  1273-1371 sq.ft   

            UnitType                            namesfull  
0    1 BHK Apartment  Salarpuria Sattva Cadenza bangalore  
1    2 BHK Apartment  Salarpuria Sattva Cadenza bangalore  
2  2.5 BHK Apartment  Salarpuria Sattva Cadenza bangalore  
3    3 BHK Apartment  Salarpuria Sattva Cadenza bangalore  
4    2 BHK Apartment              Purva Skydale bangalore

In [7]:
#apartment_data.csv consist of data of building and their position
buildings = pd.read_csv('apartment_data.csv')

#We would have to drop columns geometry as this cant be used to plot on map
buildings = buildings.drop(columns="geometry")

#We would create of our column called location
buildings['location'] = list(zip(buildings.lat, buildings.lon))

#Since lat and lon column are now usefull we can drop them
buildings = buildings.drop(columns=["lat","lon"])

buildings.head()

names  \
0               Purva Skydale bangalore   
1   Salarpuria Sattva Cadenza bangalore   
2             Shriram Summitt bangalore   
3               Shriram Luxor bangalore   
4  Ecolife Elements Of Nature bangalore   

                                  location  
0           (12.894033, 77.66236169999998)  
1           (12.889441, 77.64022109999998)  
2         (12.836067800000002, 77.6672418)  
3  (13.085249000000001, 77.65491540000001)  
4          (12.9387277, 77.73112619999998)

#### Map development begins

##### First we would load the basic map of the bangalore city we want

In [8]:
BAN_COORDINATES = (12.9716, 77.5946) #coordinates of the bangalore city
bangalore_map = folium.Map(location=BAN_COORDINATES, zoom_start=12, max_zoom = 16) #map of bangalore
bangalore_json = os.path.join('bbmp.json') #Loading the json file of bangalore

bangalore_map

##### Adding a geojson layer on top of the map

In [9]:
"""
We add a geojson layer on top of the map. 
On hovering now, we can see the ward name and ward number.
"""
bangalore_geojson = folium.GeoJson(bangalore_json, name='bangalore',
        tooltip= features.GeoJsonTooltip(fields= ['WARD_NAME', 'WARD_NO'],
            labels=True, 
            sticky=True
        )).add_to(bangalore_map)
bangalore_map

##### Adding search based on ward_name in the map

In [10]:
ward_search = plugins.Search(layer=bangalore_geojson,
        geom_type='Polygon',
        placeholder='Search for bangalore wards',
        collapsed=False,
        search_label='WARD_NAME'
        ).add_to(bangalore_map)
bangalore_map

##### Adding markers and there popups on the map

<ul>
    <li> Since the records consist of a lot of data, we would only consider the first 1300 rows for the project </li>
    <li> First on your own loop throught the buildings dataframe once using iterrows() method </li>
    <li> You will find The 0th column is the index while the columns in the first column are out required columns</li>
    <li> For each building, we will put a marker on a map and a popup which will show apartments as shown in indiviual_apartments dataframe
</ul>

In [43]:
max_records = 1300

#Create a markers 
markers = plugins.MarkerCluster(control=False)
for building in buildings[0:max_records].iterrows():
    text = '<h4>' + building[1]['names'] + '</h4>'
    popup_table = Indiviual_apartments[Indiviual_apartments.namesfull == building[1]['names']].loc[:, ['Price', 'Area', 'UnitType']]
    popup_data = text + popup_table.to_html(classes="table table-striped table-hover table condensed table-responsive",index=False)
    foliumMarker(
        popup = Popup(popup_data, max_width = 400),
        location = [building[1].location[0], building[1].location[1]]
    ).add_to(markers)
    
markers.add_to(bangalore_map)
    


bangalore_map


##### Add a layer Control and save this file as html
<ul>
    <li> Layer Control allows to hide/show json geojson layer </li>
</ul>

In [44]:
LayerControl().add_to(bangalore_map)
bangalore_map.save('bangalore_map.html')